#  Instalação de pacotes e imports necessários


In [1]:
# %% [code]
# Instalações e imports
!pip install pmdarima requests statsmodels --quiet
!pip install plotly pmdarima statsmodels --quiet


import io
import re
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import os
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import requests
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.stattools import adfuller, kpss
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
from IPython.display import display, Markdown

sns.set(style="whitegrid")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 15.0 MB/s eta 0:00:00


#   Download dos Dados do GitHub


In [2]:
# %% [code]
# Configuração do download
url_repo = "https://api.github.com/repos/PedroCosDi/estudos_ia/contents/aprendizado_supervisionado/queimadas_serie_temporal/dados/processados"
pasta_destino = "/content/processados/"
os.makedirs(pasta_destino, exist_ok=True)

# Função de download
def baixar_dados():
    arquivos = requests.get(url_repo).json()
    for arquivo in arquivos:
        if arquivo['name'].endswith('.csv'):
            conteudo = requests.get(arquivo['download_url']).content
            with open(os.path.join(pasta_destino, arquivo['name']), 'wb') as f:
                f.write(conteudo)
            print(f"Arquivo baixado: {arquivo['name']}")

baixar_dados()

Arquivo baixado: AC_final.csv
Arquivo baixado: AL_final.csv
Arquivo baixado: AM_final.csv
Arquivo baixado: AP_final.csv
Arquivo baixado: BA_final.csv
Arquivo baixado: CE_final.csv
Arquivo baixado: DF_final.csv
Arquivo baixado: ES_final.csv
Arquivo baixado: GO_final.csv
Arquivo baixado: MA_final.csv
Arquivo baixado: MG_final.csv
Arquivo baixado: MS_final.csv
Arquivo baixado: MT_final.csv
Arquivo baixado: PA_final.csv
Arquivo baixado: PB_final.csv
Arquivo baixado: PE_final.csv
Arquivo baixado: PI_final.csv
Arquivo baixado: PR_final.csv
Arquivo baixado: RJ_final.csv
Arquivo baixado: RN_final.csv
Arquivo baixado: RO_final.csv
Arquivo baixado: RR_final.csv
Arquivo baixado: RS_final.csv
Arquivo baixado: SC_final.csv
Arquivo baixado: SE_final.csv
Arquivo baixado: SP_final.csv
Arquivo baixado: TO_final.csv


#  Carregar DataFrames


In [3]:
# %% [code]
# Carregar DataFrames e listar estados
dataframes = {
    arquivo.split('_')[0]: pd.read_csv(
        os.path.join(pasta_destino, arquivo),
        index_col=0,
        parse_dates=True
    )
    for arquivo in os.listdir(pasta_destino)
    if arquivo.endswith('_final.csv')
}

estados = sorted(dataframes.keys())
print("Estados carregados:", estados)

Estados carregados: ['AC', 'AL', 'AM', 'AP', 'BA', 'CE', 'DF', 'ES', 'GO', 'MA', 'MG', 'MS', 'MT', 'PA', 'PB', 'PE', 'PI', 'PR', 'RJ', 'RN', 'RO', 'RR', 'RS', 'SC', 'SE', 'SP', 'TO']


#   Função de Análise Exploratória (EDA)


In [4]:
# %% [code]
def eda_interativo_final(df, estado):
    """EDA interativo completo com resumo técnico integrado"""

    display(Markdown(f"# 📍 {estado}"))

    # ================== 1. RESUMO TÉCNICO (INFO + DESCRIBE) ==================
    display(Markdown("## 📋 Resumo Técnico"))

    # Info() formatado
    buffer = io.StringIO()
    df.info(buf=buffer, verbose=True, show_counts=True)
    info_output = buffer.getvalue().replace('non-null', '✅ non-null').replace('dtype:', '📊 dtype:')
    display(Markdown(f"```\n{info_output}\n```"))

    # Describe() estilizado
    desc = df.describe(include='all').T.style \
        .format(precision=2, na_rep="-") \
        .background_gradient(cmap='YlOrBr', subset=['mean', 'std', '50%']) \
        .bar(subset=['min', 'max'], color='#ff7f0e')
    display(desc)

    # ================== 2. TESTES DE ESTACIONARIEDADE PARA TODAS AS COLUNAS ==================
    display(Markdown("## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)"))

    # Lista para armazenar resultados
    resultados = []

    for coluna in df.columns:
        if pd.api.types.is_numeric_dtype(df[coluna]):
            try:
                serie = df[coluna].dropna()

                # Teste ADF
                adf_result = adfuller(serie)
                adf_p = adf_result[1]

                # Teste KPSS
                kpss_result = kpss(serie, regression='c')
                kpss_p = kpss_result[1]

                # Interpretação
                resultado = {
                    'Coluna': coluna,
                    'ADF p-value': f"{adf_p:.4f}",
                    'ADF': "✅ Estacionária" if adf_p < 0.05 else "❌ Não Estacionária",
                    'KPSS p-value': f"{kpss_p:.4f}",
                    'KPSS': "✅ Estacionária" if kpss_p > 0.05 else "❌ Não Estacionária",
                    'Conclusão': ""
                }

                # Lógica combinada
                if adf_p < 0.05 and kpss_p > 0.05:
                    resultado['Conclusão'] = "✅ Estritamente Estacionária"
                elif adf_p < 0.05 or kpss_p > 0.05:
                    resultado['Conclusão'] = "⚠️ Estacionariedade Parcial"
                else:
                    resultado['Conclusão'] = "❌ Não-Estacionária"

                resultados.append(resultado)

            except Exception as e:
                resultados.append({
                    'Coluna': coluna,
                    'ADF p-value': f"Erro: {str(e)}",
                    'ADF': "-",
                    'KPSS p-value': "-",
                    'KPSS': "-",
                    'Conclusão': "⚠️ Teste Falhou"
                })

    # Criar e formatar tabela
    df_resultados = pd.DataFrame(resultados)

    if not df_resultados.empty:
        estilo = df_resultados.style \
            .hide(axis="index") \
            .set_properties(**{'text-align': 'left'}) \
            .set_table_styles([{
                'selector': 'th',
                'props': [('text-align', 'left')]
            }]) \
            .applymap(lambda x: 'color: #4CAF50' if '✅' in str(x) else 'color: #f44336' if '❌' in str(x) else '',
                      subset=['ADF', 'KPSS', 'Conclusão'])

        display(estilo)
    else:
        display(Markdown("Nenhuma coluna numérica para testar."))

    # ================== 3. SÉRIE TEMPORAL INTERATIVA ==================
    if 'FOCOS DE QUEIMADA' in df.columns:
        display(Markdown("## 📈 Série Temporal dos Focos de Queimada"))
        fig = px.line(df, x=df.index, y='FOCOS DE QUEIMADA',
                      title=f'Focos de Queimada em {estado}',
                      labels={'value': 'Focos'},
                      hover_data={'FOCOS DE QUEIMADA': ':.0f'})
        fig.update_layout(template='plotly_white', hovermode='x')
        fig.show()

    # ================== 4. DECOMPOSIÇÃO SAZONAL ==================
    if 'FOCOS DE QUEIMADA' in df.columns:
        display(Markdown("## 📅 Decomposição Sazonal (Focos)"))
        try:
            decomp = seasonal_decompose(df['FOCOS DE QUEIMADA'], model='additive', period=12)
            fig = make_subplots(rows=4, cols=1, shared_xaxes=True,
                               subplot_titles=("Observado", "Tendência", "Sazonalidade", "Resíduos"))

            fig.add_trace(go.Scatter(x=df.index, y=decomp.observed, name='Observado'), row=1, col=1)
            fig.add_trace(go.Scatter(x=df.index, y=decomp.trend, name='Tendência'), row=2, col=1)
            fig.add_trace(go.Scatter(x=df.index, y=decomp.seasonal, name='Sazonalidade'), row=3, col=1)
            fig.add_trace(go.Scatter(x=df.index, y=decomp.resid, name='Resíduos'), row=4, col=1)

            fig.update_layout(height=600, showlegend=False)
            fig.show()
        except Exception as e:
            print(f"⚠️ Erro na decomposição: {str(e)}")

    # ================== 5. VARIÁVEIS NORMALIZADAS ==================
    if len(df.columns) > 1:
        display(Markdown("## 🌡️ Comparação de Variáveis (0-1)"))
        df_norm = (df - df.min()) / (df.max() - df.min())

        fig = px.line(df_norm, x=df_norm.index, y=df_norm.columns,
                     title='Variáveis em Escala Normalizada',
                     labels={'value': 'Valor Normalizado'})

        fig.update_layout(
            hovermode='x unified',
            legend=dict(orientation='v', yanchor='top', y=0.99, xanchor='left', x=1.02),
            margin=dict(r=150),
            height=500
        )
        fig.show()

    # ================== 6. CORRELAÇÕES ==================
    if len(df.columns) > 1:
        display(Markdown("## 🔗 Matriz de Correlação"))
        corr = df.corr().round(2)

        fig = px.imshow(corr,
                       text_auto=True,
                       color_continuous_scale='RdBu_r',
                       width=800, height=800)

        fig.update_layout(xaxis=dict(tickangle=90), font_size=10)
        fig.show()

## Clicar nas colunas dos gráficos

Os gráficos são interativos, clicando nas colunas podemos retirar ou adicionar as linhas da legenda.

## Comentário

O número reduzido de instâncias (71) prejudica a validação dos testes de estacionariedade e correlação. Essa quantidade foi escolhida porque os dados de queimadas são fornecidos em formato mensal, e séries temporais muito longas podem sofrer alterações de contexto devido a diversos fatores externos, tornando-se mais difíceis de explicar. Se os dados de queimadas fossem semanais ou diários, teríamos mais facilidade para trabalhar com eles.

#   Análise AC




In [5]:
display(Markdown("# 🟥 Acre"))
df_ac = dataframes['AC']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_ac, 'AC')

# 🟥 Acre

# 📍 AC

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning: The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.

  kpss_result = kpss(serie, regression='c')
<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning: The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.

  kpss_result = kpss(serie, regression='c')
<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning: The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.

  kpss_result = kpss(serie, regression='c')
<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning: The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.

  kpss_result = kpss(serie, regression='c')
<ipython-input-4

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise AL

In [6]:
display(Markdown("# 🟥 Alagoas"))
df_al = dataframes['AL']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_al, 'AL')

# 🟥 Alagoas

# 📍 AL

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise AM

In [7]:
display(Markdown("# 🟥 Amazonas"))
df_am = dataframes['AM']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_am, 'AM')

# 🟥 Amazonas

# 📍 AM

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise AP

In [8]:
display(Markdown("# 🟥 Amapá"))
df_ap = dataframes['AP']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_ap, 'AP')

# 🟥 Amapá

# 📍 AP

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise BA



In [9]:
display(Markdown("# 🟥 Bahia"))
df_ba = dataframes['BA']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_ba, 'BA')

# 🟥 Bahia

# 📍 BA

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise CE


In [10]:
display(Markdown("# 🟥 Ceará"))
df_ce = dataframes['CE']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_ce, 'CE')

# 🟥 Ceará

# 📍 CE

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise DF

In [11]:
display(Markdown("# 🟥 Distrito Federal"))
df_df = dataframes['DF']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_df, 'DF')

# 🟥 Distrito Federal

# 📍 DF

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise ES

In [12]:
display(Markdown("# 🟥 Espírito Santo"))
df_es = dataframes['ES']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_es, 'ES')

# 🟥 Espírito Santo

# 📍 ES

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise GO

In [13]:
display(Markdown("# 🟥 Goiás"))
df_go = dataframes['GO']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_go, 'GO')

# 🟥 Goiás

# 📍 GO

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise MA

In [14]:
display(Markdown("# 🟥 Maranhão"))
df_ma = dataframes['MA']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_ma, 'MA')

# 🟥 Maranhão

# 📍 MA

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise MG

In [15]:
display(Markdown("# 🟥 Minas Gerais"))
df_mg = dataframes['MG']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_mg, 'MG')

# 🟥 Minas Gerais

# 📍 MG

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise MS

In [16]:
display(Markdown("# 🟥 Mato Grosso do Sul"))
df_ms = dataframes['MS']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_ms, 'MS')

# 🟥 Mato Grosso do Sul

# 📍 MS

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise MT

In [17]:
display(Markdown("# 🟥 Mato Grosso"))
df_mt = dataframes['MT']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_mt, 'MT')

# 🟥 Mato Grosso

# 📍 MT

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise PA

In [18]:
display(Markdown("# 🟥 Pará"))
df_pa = dataframes['PA']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_pa, 'PA')

# 🟥 Pará

# 📍 PA

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:83: FutureWarning:

Styler.applymap has been deprecated. Use Styler.map instead.



## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise PB

In [19]:
display(Markdown("# 🟥 Paraíba"))
df_pb = dataframes['PB']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_pb, 'PB')

# 🟥 Paraíba

# 📍 PB

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise PE

In [20]:
display(Markdown("# 🟥 Pernambuco"))
df_pe = dataframes['PE']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_pe, 'PE')

# 🟥 Pernambuco

# 📍 PE

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise PI

In [21]:
display(Markdown("# 🟥 Piauí"))
df_pi = dataframes['PI']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_pi, 'PI')

# 🟥 Piauí

# 📍 PI

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise PR

In [22]:
display(Markdown("# 🟥 Paraná"))
df_pr = dataframes['PR']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_pr, 'PR')

# 🟥 Paraná

# 📍 PR

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise RJ

In [23]:
display(Markdown("# 🟥 Rio de Janeiro"))
df_rj = dataframes['RJ']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_rj, 'RJ')

# 🟥 Rio de Janeiro

# 📍 RJ

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise RN

In [24]:
display(Markdown("# 🟥 Rio Grande do Norte"))
df_rn = dataframes['RN']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_rn, 'RN')

# 🟥 Rio Grande do Norte

# 📍 RN

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise RO

In [25]:
display(Markdown("# 🟥 Rondônia"))
df_ro = dataframes['RO']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_ro, 'RO')

# 🟥 Rondônia

# 📍 RO

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise RR

In [26]:
display(Markdown("# 🟥 Roraima"))
df_rr = dataframes['RR']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_rr, 'RR')

# 🟥 Roraima

# 📍 RR

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise RS

In [27]:
display(Markdown("# 🟥 Rio Grande do Sul"))
df_rs = dataframes['RS']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_rs, 'RS')

# 🟥 Rio Grande do Sul

# 📍 RS

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise SC

In [28]:
display(Markdown("# 🟥 Santa Catarina"))
df_sc = dataframes['SC']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_sc, 'SC')

# 🟥 Santa Catarina

# 📍 SC

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise SE

In [29]:
display(Markdown("# 🟥 Sergipe"))
df_se = dataframes['SE']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_se, 'SE')

# 🟥 Sergipe

# 📍 SE

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     float64
dtypes: float64(17)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise SP

In [30]:
display(Markdown("# 🟥 São Paulo"))
df_sp = dataframes['SP']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_sp, 'SP')

# 🟥 São Paulo

# 📍 SP

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação

#   Análise TO

In [31]:
display(Markdown("# 🟥 Tocantins"))
df_to = dataframes['TO']
# Dentro da função eda_interativo_final:
eda_interativo_final(df_to, 'TO')

# 🟥 Tocantins

# 📍 TO

## 📋 Resumo Técnico

```
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 71 entries, 2019-01-31 to 2024-11-30
Data columns (total 17 columns):
 #   Column                                                Non-Null Count  Dtype  
---  ------                                                --------------  -----  
 0   PRECIPITAÇÃO TOTAL, MENSAL (MM)                       71 ✅ non-null     float64
 1   PRESSAO ATMOSFERICA AO NIVEL DA ESTACAO, MENSAL (MB)  71 ✅ non-null     float64
 2   PRESSÃO ATMOSFERICA MAX.MENSAL (AUT) (MB)             71 ✅ non-null     float64
 3   PRESSÃO ATMOSFERICA MIN. MENSAL (AUT) (MB)            71 ✅ non-null     float64
 4   RADIACAO GLOBAL (KJ/M²)                               71 ✅ non-null     float64
 5   TEMPERATURA DO AR - BULBO SECO, MENSAL (°C)           71 ✅ non-null     float64
 6   TEMPERATURA DO PONTO DE ORVALHO (°C)                  71 ✅ non-null     float64
 7   TEMPERATURA MÁXIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 8   TEMPERATURA MÍNIMA MENSAL (AUT) (°C)                  71 ✅ non-null     float64
 9   TEMPERATURA ORVALHO MAX. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 10  TEMPERATURA ORVALHO MIN. MENSAL (AUT) (°C)            71 ✅ non-null     float64
 11  UMIDADE REL. MAX. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 12  UMIDADE REL. MIN. MENSAL (AUT) (%)                    71 ✅ non-null     float64
 13  UMIDADE RELATIVA DO AR, MENSAL (%)                    71 ✅ non-null     float64
 14  VENTO, RAJADA MAXIMA (M/S)                            71 ✅ non-null     float64
 15  VENTO, VELOCIDADE MENSAL (M/S)                        71 ✅ non-null     float64
 16  FOCOS DE QUEIMADA                                     71 ✅ non-null     int64  
dtypes: float64(16), int64(1)
memory usage: 10.0 KB

```

## 📉 Testes de Estacionariedade (Todas Colunas Numéricas)

<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.


<ipython-input-4-1bd536feb1ee>:39: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the 

## 📈 Série Temporal dos Focos de Queimada

## 📅 Decomposição Sazonal (Focos)

## 🌡️ Comparação de Variáveis (0-1)

## 🔗 Matriz de Correlação